## Toffoli kapu


<div class="alert alert-block">

**Cél**

Építsd meg a Toffoli kapu áramkörét a IBM kvantumszámítógépek bázis kapuiból: A CX (CNOT), RZ, SX és X kapukból. 

</div>

<div class="alert alert-block">
    
Lépésről lépésre végig haladhatsz a tutorial cellákon, illetve hogyha úgy érzed felkészültél, rögtön ugorhatsz is a <a href=#problem>»végső feladatra«</a>.
</div>

In [ ]:
# Matplotlib warningok ellen hasznos

import warnings
from matplotlib.cbook import MatplotlibDeprecationWarning
warnings.filterwarnings('ignore', category=MatplotlibDeprecationWarning)

# Standard qiskit libek importálása
from qiskit import QuantumCircuit, execute, Aer, IBMQ, QuantumRegister, ClassicalRegister
from qiskit.compiler import transpile, assemble
from qiskit.tools.jupyter import *
from qiskit.visualization import *
from ibm_quantum_widgets import *

# A kiértékelő parancsai
! pip3 install szte_qp_grader
import szte_qp_grader as grader

# Valószínűleg kelleni fog pi is
import math
pi=math.pi

In [ ]:
# Frissített kiértékelő esetén futtasd ezt a sort:
# pip install --upgrade szte-qp-grader

## Gyakorlás: kvantum kapuk

A kvantum áramkörök, amikből az algoritmusainkat építhetjük, kapukból épülnek fel. A kapukat felfoghatjuk forgatásként is a Bloch gömb felszínén. Nézzünk meg pár alapvető kaput.

### X kapu 

Az X kapu mátrixa: 

$X = \begin{pmatrix}
0 & 1 \\
1 & 0 \\
\end{pmatrix}$

Az X kapu egy forgatás a Bloch gömb X tengelye körül $\pi$ radiánnal (180 fokkal). A $|0\rangle$ állapotból $|1\rangle$ állapotot hoz létre, az $|1\rangle$ állapotból $|0\rangle$-t.

In [ ]:
x_gate=QuantumCircuit(1) # Kvantum áramkör létrehozása 1 bittel
x_gate.x(0)
x_gate.draw(output='mpl')

In [ ]:
# Nézzük ezt a Bloch gömbön is
backend = Aer.get_backend('statevector_simulator')
result = execute(x_gate, backend).result().get_statevector()
plot_bloch_multivector(result)

### SX kapu

Az SX kapu (Square root X) vagy $\sqrt{X}$ kapu forgatás az X tengely körül $\pi/2$-vel. Gyök X, mert ha kétszer hajtjuk végre egymás után, akkor pont az X kaput kapjuk. Ez matematikailag összeszorozná tehát a kapukat egymás után. Az SX kapu inverze, tehát a másik irányú forgatás az "SX dagger" kapu, ami csak ugyanaz a forgatás, $-\pi/2$-vel.

$SX = \frac{1}{2}\begin{pmatrix}
1+i & 1-i \\
1-i & 1+i \\
\end{pmatrix}$

In [ ]:
sx_gate = QuantumCircuit(1)
sx_gate.sx(0)  
sx_gate.draw(output='mpl')

In [ ]:
backend = Aer.get_backend('statevector_simulator')
result = execute(sx_gate, backend).result().get_statevector()
plot_bloch_multivector(result)

### RZ kapu

Az Rz kapu egy paraméteres forgatás kapu a Z tengely körül, $\phi$ radiánnal.

$RZ = \begin{pmatrix}
1 & 0 \\
0 & e ^{i \phi } \\
\end{pmatrix}$

Melyik kaput kapjuk meg, ha $\phi = \pi$?

In [ ]:
rz_gate = QuantumCircuit(1)
rz_gate.rz(pi/2, 0)
rz_gate.draw(output='mpl')

In [ ]:
backend = Aer.get_backend('statevector_simulator')
result = execute(rz_gate, backend).result().get_statevector()
plot_bloch_multivector(result)

Mivel a Z tengely körüli forgatás nem látszana a $|0\rangle$ állapoton, mert az pont a Z tengelyre esik, elforgatjuk onnan az állapotot, hogy lássuk mit is csinálnak a kapuink.

In [ ]:
rz_gate.sx(0)
rz_gate.rz(pi/2, 0)
rz_gate.draw(output='mpl')

In [ ]:
backend = Aer.get_backend('statevector_simulator')
result = execute(rz_gate, backend).result().get_statevector()
plot_bloch_multivector(result)

### Hadamard kapu

A Hadamard kapu egy tükrözés az X és Z tengelyek között félúton lévő tengely körül. Ez a kapu a $|0\rangle$ bázisállapotot a $\frac{|0\rangle + |1\rangle}{\sqrt{2}}$ állapottá változtatja. Ezt az állapotot hívjuk $|+\rangle$ állapotnak. 

A Hadamard kapu bázis vált a $|0\rangle$ $|1\rangle$ bázis és a  $|+\rangle$ $|-\rangle$ bázis között.

$H = \frac{1}{\sqrt{2}}\begin{pmatrix}
1 & 1 \\
1 & -1 \\
\end{pmatrix}$

In [ ]:
h_gate = QuantumCircuit(1)
h_gate.h(0)
h_gate.draw(output='mpl')

In [ ]:
backend = Aer.get_backend('statevector_simulator')
result = execute(h_gate, backend).result().get_statevector()
plot_bloch_multivector(result)

### CX kapu (CNOT kapu)

A CX vagy CNOT kapu olyasmi, mint egy `if` szerkezet. Két qubitre hat, az egyik a control bit, a másik a target. Ha a control $|1\rangle$ akkor negálja a targetet (azaz végrehajtja rajta az X kaput).

Note: Qiskit jobbról balra indexeli a biteket (nagy endián).

$CX = \begin{pmatrix}
1 & 0 & 0 & 0  \\
0 & 1 & 0 & 0 \\
0 & 0 & 0 & 1 \\
0 & 0 & 1 & 0 \\
\end{pmatrix}$

In [ ]:
cx_gate = QuantumCircuit(2)
cx_gate.cx(0,1)
cx_gate.draw(output='mpl')

### CCX kapu (Toffoli kapu)

A CCX kapu nagyjából az éselést valósítja meg. Ha a két control bit $|1\rangle$ állapotban van, negálja a target bitet.

$CCX = \begin{pmatrix}
1 & 0 & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 1 & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & 1 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & 0 & 1 & 0 & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 1 & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 1 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & 0 & 1 \\
0 & 0 & 0 & 0 & 0 & 0 & 1 & 0 \\
\end{pmatrix}$

In [ ]:
ccx_gate = QuantumCircuit(3)
ccx_gate.ccx(0,1,2)
ccx_gate.draw(output='mpl')

## Klasszikus logikai kapuk kvantum kapukkal

### NOT kapu

A NOT kapu csak negálja a bit értékét, pontosan mint a mi X kapunk.

| Input | Output |
| --- | --- | 
| 1 | 0 |
| 0 | 1 |

In [ ]:
not_gate=QuantumCircuit(1,1) 
not_gate.x(0)
not_gate.measure(0,0)
not_gate.draw(output='mpl')

### AND kapu (ÉS)

Az output 1 akkor és csak akkor ha mindkét input 1.

| A (Input) | B (Input) | Output |
| --- | --- | --- |
| 0 | 0 | 0 | 
| 0 | 1 | 0 |
| 1 | 0 | 0 |
| 1 | 1 | 1 |

Toffoli kapuval meg tudjuk kapni az eredményt, ha a control biteket tekintjük input bitnek és a target bitet outputnak.

In [ ]:
and_gate=QuantumCircuit(3,1) # Kvantum áramkör 3 qubittel és 1 bittel
and_gate.ccx(0,1,2)
and_gate.measure(2,0)
and_gate.draw(output='mpl')

### OR kapu (VAGY)

A VAGY kapu akkor ad vissza 1-et, ha az input bitek valamelyike 1.
Az igazságtáblája:

| A (Input) | B (Input) | Output |
| --- | --- | --- |
| 0 | 0 | 0 | 
| 0 | 1 | 1 |
| 1 | 0 | 1 |
| 1 | 1 | 1 |

In [ ]:
or_gate=QuantumCircuit(3,1) # Kvantum áramkör 3 qubittel és 1 bittel
or_gate.cx(1,2)
or_gate.cx(0,2)
or_gate.ccx(0,1,2)
or_gate.measure(2,0)
or_gate.draw(output='mpl')

## A Circuit Composer widget használata

<div class="alert alert-block alert-success">

**1/a feladat:**  Építs egy NOR kaput (NEM-VAGY kaput) a circuit composer használatával! 
</div>

In [ ]:
from ibm_quantum_widgets import CircuitComposer
editor = CircuitComposer()
editor

### Circuit Composer használata egy létező áramkör módosításához

A kézzel megírt áramköröket is át lehet pakolni a composerbe, csak az konstuktor 'circuit' paraméterét kell beállítani.

<div class="alert alert-block alert-success">

Tudod szerkeszteni drag and droppal. Próbáld meg kitörölni az utolsó mérést!
    
</div>

In [ ]:
from ibm_quantum_widgets import CircuitComposer
editor2 = CircuitComposer(circuit=or_gate)
editor2

Ezt pl így tudjuk implementálni, vagy kóddá alakítani, használva az editor circuit propertyjét.

In [ ]:
qc2 = editor2.circuit

qc2.x(2)
qc2.measure((2), (0))

qc2.draw(output='mpl')

A NOR kapu megoldása itt látható fent, az előző feladathoz ilyesmit kellett kapnod. Ugyankkor ez a minimális megoldás csak, hosszabb, ugyanúgy ezzel ekvivalens áramkörök is léteznek.

## Összetett kvantum kapuk és kiszámítási áruk

Egy igazi kvantumszámítógépen nincs meg az összes kvantum kapu fizikai implementációja, csak azoknak egy részhalmaza (amikkel persze minden egyéb kapu kiszámítható).

Ezért a megépített kvantum áramkörök fordításkor át lesznek alakítva az adott kvantumszámítógép báziskapuiból álló, ekvivalens áramkörre. Persze ez a fordítás némi overheaddel jár, növeli az áramkör hosszát, csökkentheti a számítás pontosságát.

Az IBM gépein általában a bázist alkotó kapuk a CX, ID (identity), Rz, SX és X kapuk. 

Egy példa: [`ibmq_mumbai`](https://quantum-computing.ibm.com/services?skip=0&systems=all&system=ibmq_mumbai)

Nézzük a következő áramkört:

In [ ]:
qc = QuantumCircuit(2)
qc.sxdg(0) # SX dagger kapu, ez az SX kapu inverze
# Óráról emlékezető: T kapu egy negyed forgatás a Z tengely körül. 
# másik emlékeztető: a Z tengelyen az "X kapu megfelelője, azaz pi forgatás az a Z kapu. 
# Ennek a fele, azaz gyök(Z) = S kapu. Ez pi/2 forgatás a Z tengely körül. Ennek a fele, azaz negyed forgatás a T kapu."
qc.t(1) 
qc.draw(output='mpl')

Ez a két kapu mire is fordul át fizikailag? Lássuk:

In [ ]:
qc = QuantumCircuit(2)
# sxdg = sx*sx*sx, mert egy -pi/2 forgatás az pont 3 * pi/2 forgatás adott irányban. (hint: egység-kör)
qc.sx(0)
qc.sx(0)
qc.sx(0) 

# t = Rz(pi/4), valóban egy negyed forgatásról van szó 
qc.rz(pi/4,1) 
qc.draw(output='mpl')

Ahogy látható, sikerült felírni az áramkört a bázis kapukkal, viszont ezzel költségesebb is lett (több kaput használtunk fel). Viszont nem minden kapunak egységes a költsége. A két qubites kapuk sokkal lassabbak és pontatlanabbak, ezért a következő formulát vezetjük most be:

$$
\text{Költség} = 10 N_{CNOT} + N_{egyéb}
$$

ahol $N_{CNOT}$ a CNOT kapuk száma, és $N_{other}$ a többi kapu száma.

### Hadamard kapu

Minden kapunk kifejezhető bázis kapukkal. Ugyanakkor a Hadamard kapu forgatására nincs egy kapunk. Hogyan forgathatnánk mégis "oda" az állapotunkat több forgatással, ahova a hadamard kapu teszi? 


In [ ]:
q=QuantumRegister(1)
c=ClassicalRegister(1)
qc=QuantumCircuit(q,c)
qc.rz(pi/2, 0)
qc.sx(0)
qc.rz(pi/2, 0)
qc.draw(output='mpl')

Az előbb láthattuk, hogy az Rz kapu semmit nem csinál, ha a $|0\rangle$ vagy $|1\rangle$ állapotban vagyunk. Tehát kicsit haszontalannak tűnhet. De ha a $|+\rangle$ vagy $|-\rangle$ állapotban lennénk, akkor az első Rz kapu és az SX kapu után az tuolsó Rz lenne haszontalan.

### Kontrollált forgatások

Láttunk kontrollált NOT (CNOT) kaput, most nézzük hogy lehet kontrollált forgatást összerakni az Y tengely körül. Ez a forgatás  $\theta$ lehet bármekkora, nem kell $\pi$-nek lennie, csak a példa kedvéért annyi most.

In [ ]:
qc = QuantumCircuit(2)
theta = pi # theta bármi lehetne persze
qc.ry(theta/2,1)
qc.cx(0,1)
qc.ry(-theta/2,1)
qc.cx(0,1)
qc.draw(output='mpl')

Végighaladva a kapukon, láthatjuk, hogy ha q0 0, akkor a két forgatás egymást kioltja és semmi sem történik. Míg, ha q0 épp 1, akkor kétszer fogunk forgatni $\theta / 2$-vel, tehát megkapjuk az eredeti $\theta$-val való forgatásunkat. Ez azért működik, mert az X és az Y tengely merőleges egymásra.

<div class="alert alert-block alert-danger">
Más tengelyek körüli forgatásokhoz egyéb trükkök kellhetnek.
</div>

### CCR (Kontrollált kontrollált forgatás)

A fenti forgatást megépíthetjük duplán kontrollált módon is, azaz csak akkor forgatunk, ha mindkét control bit 1.

In [ ]:
qc = QuantumCircuit(3)
theta = pi
qc.cp(theta/2,1,2)
qc.cx(0,1)
qc.cp(-theta/2,1,2) # Controlled Phase gate --- Kontrollált fázis kapu
qc.cx(0,1)
qc.cp(theta/2,0,2)
qc.draw()

Ebben az áramkörben, ha az:
  - q0 és q1 is 0 akkor nem történik semmi
  - ha csak a második qubit 1, akkor előbb egy $\pi/2$ majd egy $-\pi/2$ forgatás kiüti egymást
  - ha csak az első qibit 1, akkor a második qubit is 1 lesz az első CNOT után, tehát az első kontrollált forgatás semmit nem csinál, a további kettő pedig kiüti egymást
  - ha az első és második qubit is 1, akkor az első forgatás után az első CNOT kapu nullára állítja a második bitet, így a negatív irányú forgatás nem jön létre, csak az utolsó pozitív, így a két $pi/2$ forgatásból egy $pi$ szögű forgatásunk lesz

## A feladat

<div id='problem'></div>
<div class="alert alert-block alert-success">

A Toffoli kapu univerzális önmagában a kvantum áramkörök szempontjából, úgy, mint a NAND kapu a klasszikus áramköröknél. Ugyanakkor a Toffoli kapu reverzibilis (bijektív leképezést valósít meg, minden outputból egyértelműen az input visszakereshető.
    
A feladat tehát: implementáld a Toffoli kaput a báziskapuk segítségével!
</div>


<div class="alert alert-block alert-danger">

Kis emlékeztető: a bázis kapuk az IBM rendszerein a CX, RZ, SX és X kapuk, tehát más kaput nem használhatsz.

És természetesen a cél, hogy minimalizáld a költséget:
    
$$
\text{Költség} = 10 N_{CNOT} + N_{egyéb}
$$
    
</div>


In [ ]:
from qiskit import QuantumRegister, ClassicalRegister, QuantumCircuit
from qiskit import IBMQ, Aer, execute
from ibm_quantum_widgets import CircuitComposer
editorEx = CircuitComposer() 
editorEx
# Itt a composerrel meg tudod építeni az áramköröd

In [ ]:
# Vagy itt a Qiskit kód segítségével szintén

circuit = QuantumCircuit(3)

# A KÓDOD ITT KEZDŐDJÖN - START




# A KÓDOD ITT VÉGZŐDJÖN - END

In [ ]:
# Az eredmény mutatása
qc = editorEx.circuit 
# qc = circuit # Vedd ki a komment jelet, ha kóddal, és nem a composerrel írtad

qc.draw(output='mpl')

In [ ]:
# Az eredmény ellenőrzése
LAST_NAME = "None" # Ide írd be a vezetékneved ékezetek nélkül!

# beküldés
grader.ex1(LAST_NAME, circuit)

**Feladat src:** IBM Q